In [1]:
# imports 

import pandas as pd
import numpy as np
import sys

In [2]:
# constants (drug names)
pain_drugs = ['Codeine',
 'Codeine Phosphate',
 'Codeine Sulfate',  'Fentanyl',
 'Fentanyl ',
 'Fentanyl Citrate',
 'Fentanyl PCA',
 'Fentanyl Patch','FENTANYL',
  'HYDROMORPHONE',
              'Hydrocodone-Acetaminophen',
 'Hydrocodone-Acetaminophen (5mg-500mg',
 'Hydrocodone-Acetaminophen (5mg-500mg)',
 'HYDROmorphone',
 'HYDROmorphone (Dilaudid)',
 'HYDROmorphone Infusion ? Comfort Care Guidelines',
 'HYDROmorphone P.F.',
 'HYDROmorphone PCA',
 'HYDROmorphone PCA (Dilaudid)',
 'HYDROmorphone-HP',
'Hydromorphone',
 'Hydromorphone (Rectal)',
 'Hydromorphone HCl',
 'Hydromorphone P.F.',
 'Hydromorphone PCA',
 'Hydromorphone-HP',
 'Hydromorphone-hp',
'OxycoDONE',
 'OxycoDONE ',
 'OxycoDONE (Immediate Release) ',
 'OxycoDONE Liquid',
 'OxycoDONE-Acetaminophen Elixir',
 'OxycodONE ',
 'OxycodONE (Immediate Release) ',
 'Oxycodone',
 'Oxycodone ',
 'Oxycodone (Sustained Release)',
 'Oxycodone HCl',
 'Oxycodone Liquid',
 'Oxycodone SR (OxyconTIN)',
 'Oxycodone-Acetaminophen',
 'Oxycodone-Acetaminophen (5mg-325mg)',
 'Oxycodone-Acetaminophen Elixir', 'Oxymorphone',
 'Oxymorphone HCl', 'MORPHINE SULFATE', 'Morphine',
 'Morphine ',
 'Morphine (PF)',
 'Morphine Infusion ? Comfort Care Guidelines',
 'Morphine PCA',
 'Morphine S',
 'Morphine SR (MS Contin)',
 'Morphine Sulfa',
 'Morphine Sulfat',
 'Morphine Sulfate',
 'Morphine Sulfate ',
 'Morphine Sulfate (0.5-4mg)',
 'Morphine Sulfate (1-5mg)',
 'Morphine Sulfate (2-4mg)',
 'Morphine Sulfate (2-5mg)',
 'Morphine Sulfate (2-6mg)',
 'Morphine Sulfate (4-8mg)',
 'Morphine Sulfate (Concentrated Oral Soln)',
 'Morphine Sulfate (Immediate Release)',
 'Morphine Sulfate (Oral Soln.)',
 'Morphine Sulfate (PF)',
 'Morphine Sulfate (Syringe)',
 'Morphine Sulfate For Inhalation',
 'Morphine Sulfate IR',
 'Morphine Sulfate PF',
 'Morphine Sulfate SR','Vicodin ',]

In [149]:
# load data
df = pd.read_csv("./data/ADMISSIONS.csv")
df2 = pd.read_csv("./data/PRESCRIPTIONS.csv")

In [162]:
## Result: 
##      p_final and adm_final both represent the same 4026 patients that have been filtered. There are 5 ethnic
##      groups (WHITE, BLACK, ASIAN, HISPANIC, MIDDLE EASTERN) with (3272, 422, 135, 182, 15) patients respectively.
##      p_final: Pandas DataFrame that includes the (opiod) prescription information for 4026 patients
##      adm_final: Pandas DataFrame that includes the admission information for 4026 patients
##

## Need to run the first and second phase of filtration to generate
## generate the Admission table w/ filters and cross checking w/ prescription

# simplify ethnicity names first
df_table = dict()
WHITE = ["WHITE"]
BLACK = ["BLACK"]
ASIAN = ["ASIAN", "PACIFIC"]
HISPANIC = ["HISPANIC", "SOUTH AMERICAN", "PORTUGESE"]
# ARAB = ["MIDDLE EASTERN"] to few ARAB
eth_types = [WHITE, BLACK, ASIAN, HISPANIC]
for e in eth_types: 
    for i, name in enumerate(e):
        new_df = df.loc[df.ETHNICITY.str.contains(name)]
        df_tmp = new_df if i == 0 else pd.concat([df_tmp, new_df])
    df_tmp.ETHNICITY = e[0]
    df_table[e[0]] = df_tmp
a = list(df_table.values())
df_simple = pd.concat(a)
df_simple = df_simple[df_simple.ADMISSION_TYPE != "NEWBORN"] # Focus on Urgent, Emergency, Elective


# find the common diagnosis between ethnic groups in the dataset
df_diag = df_simple.dropna(axis=0, subset=['DIAGNOSIS'])
df_diag = df_diag.drop_duplicates(subset='SUBJECT_ID', keep='first') # drop duplicate rows that are same SUBJECT_ID
df_diag.DIAGNOSIS = df_diag.DIAGNOSIS.apply(lambda x: x.lower())

d_white = set(df_diag[df_diag.ETHNICITY=='WHITE'].DIAGNOSIS.value_counts().index)
d_asian = set(df_diag[df_diag.ETHNICITY=='ASIAN'].DIAGNOSIS.value_counts().index)
d_black = set(df_diag[df_diag.ETHNICITY=='BLACK'].DIAGNOSIS.value_counts().index)
d_hispanic = set(df_diag[df_diag.ETHNICITY=='HISPANIC'].DIAGNOSIS.value_counts().index)
# d_mideast = set(df_diag[df_diag.ETHNICITY=='MIDDLE EASTERN'].DIAGNOSIS.value_counts().index)

common = list(d_white.intersection(d_asian, d_black, d_hispanic))
print("num common diseases: ", len(common))
df_common = df_diag[df_diag.DIAGNOSIS.isin(common)]

# generate prescriptions dataframe

p_cohort = df2[df2['DRUG'].isin(pain_drugs)]
HADM = df_common.HADM_ID
p_final = p_cohort[p_cohort.HADM_ID.isin(HADM)]

HADM_drugs = p_final.HADM_ID
adm_final = df_common[df_common.HADM_ID.isin(HADM_drugs)]


# check distribution of diagnosis among ethnic groups
eth = ["WHITE", "BLACK", "ASIAN", "HISPANIC"]
tmp = []
for e in eth:
    df_tmp = df_common[df_common.ETHNICITY == e]
    tmp.append(df_tmp.DIAGNOSIS.value_counts()/sum(df_tmp.DIAGNOSIS.value_counts().values))
pd.DataFrame(tmp, eth).T

num common diseases:  116


WHITE     BLACK  \
pneumonia                                           0.059628  0.073540   
sepsis                                              0.043150  0.051190   
intracranial hemorrhage                             0.042300  0.023071   
coronary artery disease                             0.042130  0.009373   
chest pain                                          0.038223  0.039654   
coronary artery disease\coronary artery bypass ...  0.036524  0.012257   
gastrointestinal bleed                              0.030918  0.033165   
congestive heart failure                            0.029644  0.059120   
altered mental status                               0.028370  0.039654   
s/p fall                                            0.026841  0.010094   
subarachnoid hemorrhage                             0.025567  0.020187   
coronary artery disease\coronary artery bypass ...  0.023019  0.008652   
abdominal pain                                      0.021745  0.032444   
upper gi bleed                                      0.021575  0.031723   
stroke;telemetry;transient ischemic attack          0.019366  0.022350   
lower gi bleed                                      0.017413  0.025234   
fever                                               0.015204  0.025234   
hypotension                                         0.013845  0.022350   
s/p motor vehicle accident                          0.013845  0.004326   
subdural hematoma                                   0.013845  0.007210   
blunt trauma                                        0.013251  0.006489   
acute subdural hematoma                             0.013081  0.000721   
diabetic ketoacidosis                               0.012996  0.041817   
pancreatitis                                        0.012146  0.006489   
acute coronary syndrome                             0.012146  0.007210   
seizure                                             0.011892  0.020908   
overdose                                            0.011042  0.006489   
coronary artery disease\cath                        0.010872  0.001442   
acute renal failure                                 0.010108  0.023071   
myocardial infarction                               0.009768  0.003605   
upper gastrointestinal bleed                        0.009683  0.010094   
liver failure                                       0.008834  0.007931   
respiratory failure                                 0.008579  0.007210   
head bleed                                          0.008409  0.005768   
acute myocardial infarction                         0.007814  0.002163   
brain mass                                          0.007560  0.002884   
shortness of breath                                 0.007475  0.012257   
unstable angina                                     0.007390  0.003605   
dyspnea                                             0.007305  0.007210   
chest pain\cath                                     0.007135  0.000721   
lower gastrointestinal bleed                        0.006965  0.015141   
cholangitis                                         0.006880  0.003605   
cardiac arrest                                      0.006710  0.007210   
gi bleed                                            0.006625  0.007210   
cellulitis                                          0.006540  0.004326   
aortic dissection                                   0.006540  0.010815   
brain tumor/sda                                     0.006371  0.003605   
stroke/tia                                          0.006201  0.005768   
abdominal aortic aneurysm/sda                       0.006116  0.000721   
hyponatremia                                        0.005776  0.002884   
esophageal ca/sda                                   0.005436  0.001442   
pulmonary embolis                                   0.005266  0.007931   
cerebrovascular accident                            0.005181  0.005047   
weakness                                            0.00509

In [211]:
p_final

ROW_ID  SUBJECT_ID  HADM_ID  ICUSTAY_ID            STARTDATE  \
42       2122405          13   143045    263738.0  2167-01-09 00:00:00   
45       2122400          13   143045    263738.0  2167-01-09 00:00:00   
377      1388229          21   109451    217847.0  2134-09-14 00:00:00   
473      2123165          13   143045    263738.0  2167-01-12 00:00:00   
614      2981121          11   194540    229441.0  2178-04-17 00:00:00   
618      2981124          11   194540         NaN  2178-04-21 00:00:00   
622      2981129          11   194540         NaN  2178-04-21 00:00:00   
646      2981139          11   194540         NaN  2178-04-24 00:00:00   
668      2981152          11   194540         NaN  2178-05-03 00:00:00   
968      1968634          20   157681         NaN  2183-04-28 00:00:00   
971      1968631          20   157681         NaN  2183-04-28 00:00:00   
972      1968630          20   157681         NaN  2183-04-28 00:00:00   
1000     1967944          20   157681    264490.0  2183-04-29 00:00:00   
1019     1388983          21   109451         NaN  2134-09-11 00:00:00   
1222     1380463          28   162569    225559.0  2177-09-01 00:00:00   
1225     1380461          28   162569    225559.0  2177-09-01 00:00:00   
1240     1380485          28   162569    225559.0  2177-09-02 00:00:00   
1241     1380486          28   162569    225559.0  2177-09-02 00:00:00   
1457     1136891          23   152223    227807.0  2153-09-03 00:00:00   
1459     1136893          23   152223    227807.0  2153-09-03 00:00:00   
1497     1136132          23   152223    227807.0  2153-09-04 00:00:00   
1498     1136131          23   152223    227807.0  2153-09-04 00:00:00   
2135     1381486          36   182104    280987.0  2131-05-04 00:00:00   
2137     1381484          36   182104    280987.0  2131-05-04 00:00:00   
2138     1381483          36   182104    280987.0  2131-05-04 00:00:00   
2150     1380711          36   182104    280987.0  2131-05-05 00:00:00   
2153     1380710          36   182104    280987.0  2131-05-05 00:00:00   
2166     1380709          36   182104    280987.0  2131-05-05 00:00:00   
2803     2391776          56   181711    275642.0  2104-01-04 00:00:00   
2804     2391777          56   181711    275642.0  2104-01-04 00:00:00   
2807     2391782          56   181711         NaN  2104-01-05 00:00:00   
2808     2391783          56   181711         NaN  2104-01-05 00:00:00   
3247     1550216          68   170467    225771.0  2174-01-01 00:00:00   
3249     1550217          68   170467    225771.0  2174-01-01 00:00:00   
3569     1550244          68   170467         NaN  2173-12-21 00:00:00   
3570     1550245          68   170467         NaN  2173-12-21 00:00:00   
3571     1550246          68   170467         NaN  2173-12-21 00:00:00   
3591     1550251          68   170467         NaN  2173-12-22 00:00:00   
4035     2915821          81   175016    222874.0  2192-01-10 00:00:00   
4041     2915792          81   175016    222874.0  2192-01-11 00:00:00   
4798     2238361          96   170324         NaN  2156-03-31 00:00:00   
4817     2237594          96   170324    211943.0  2156-04-01 00:00:00   
4845     2237597          96   170324    211943.0  2156-04-07 00:00:00   
4861     2238319          96   170324    211943.0  2156-04-10 00:00:00   
4866     2238322          96   170324    211943.0  2156-04-10 00:00:00   
4883     2238327          96   170324    211943.0  2156-04-11 00:00:00   
5120      138883          98   188606         NaN  2137-04-02 00:00:00   
5121      138882          98   188606         NaN  2137-04-02 00:00:00   
5233      138889          98   188606    216929.0  2137-04-03 00:00:00   
5237      138894          98   188606    216929.0  2137-04-04 00:00:00   
5247      138897          98   188606    216929.0  2137-04-05 00:00:00   
5438     2236825          96   170324    211943.0  2156-04-19 00:00:00   
5473     2239061          96   170324         NaN  2156-04-25 00:00:00   
6519     16077

In [164]:
adm_final

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
1          22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
7          28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
15         36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
22        456         357   174486  2197-12-06 07:13:00  2198-01-03 14:00:00   
39        473         368   105889  2137-07-11 17:56:00  2137-07-16 16:00:00   
44        478         372   144383  2114-07-08 17:22:00  2114-07-16 16:00:00   
57         55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
84         82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
101        99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
103       101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
136       175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
140       179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
145       184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
150       189         140   165618  2160-09-21 08:31:00  2160-09-23 12:00:00   
153       192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
154       193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
163       202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
197       153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
199       155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
220        10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
222        12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
228        18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
229        19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
235       383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
243       391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
265       413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
272       420         330   184134  2132-01-15 07:15:00  2132-01-17 10:30:00   
285       433         340   139131  2182-01-19 18:13:00  2182-02-11 13:25:00   
293       441         348   130789  2154-12-13 12:30:00  2154-12-16 11:31:00   
304       452         354   131861  2189-02-12 18:29:00  2189-03-02 14:09:00   
323       593         468   109718  2136-02-24 13:28:00  2136-03-12 18:29:00   
325       595         470   188804  2132-04-01 12:30:00  2132-04-06 16:00:00   
336       606         480   182365  2166-08-07 14:28:00  2166-08-18 18:39:00   
341       611         485   116665  2195-02-18 18:25:00  2195-02-25 16:20:00   
342       612         487   160958  2130-10-31 12:15:00  2130-11-04 19:46:00   
344       614         489   145439  2194-09-29 19:01:00  2194-10-07 18:05:00   
349       619         494   125330  2168-02-20 23:36:00  2168-03-02 16:15:00   
366       636         509   161218  2104-05-06 03:37:00  2104-05-19 16:30:00   
369       639         511   136962  2166-11-17 19:57:00  2166-11-24 13:10:00   
379       488         383   173723  2143-08-20 18:22:00  2143-09-13 14:30:00   
407       516         404   166989  2136-03-22 20:58:00  2136-03-23 00:40:00   
409       518         406   113900  2119-08-25 22:37:00  2119-09-01 18:00:00   
421       530         414   153627  2124-04-22 14:01:00  2124-05-02 04:45:00   
437       218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
439       220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
458       239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
459       240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
464       245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
480       261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
486    

In [212]:
ms = p_final[p_final.DRUG=='Morphine Sulfate']
ms_id = ms.HADM_ID.unique()
ms_adm = adm_final[adm_final.HADM_ID.isin(ms_id)]
ms_adm.ETHNICITY.value_counts()

WHITE       5579
BLACK        514
HISPANIC     292
ASIAN        233
Name: ETHNICITY, dtype: int64

In [216]:
print(len(adm_final))
len(ms_adm)

10019


6618

In [8]:
df_tmp = pd.concat([adm_final,pd.DataFrame(columns=common)])

/usr/local/Cellar/ipython/7.0.1/libexec/vendor/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [9]:
for disease in common:
    df_tmp[disease] = (df_tmp.DIAGNOSIS == disease).astype(int)

In [10]:
df_tmp['hosp_duration'] = (df_tmp['DISCHTIME'].astype('datetime64[ns]') - df_tmp['ADMITTIME'].astype('datetime64[ns]')).dt.days

In [11]:
df_tmp.columns

Index(['ADMISSION_LOCATION', 'ADMISSION_TYPE', 'ADMITTIME', 'DEATHTIME',
       'DIAGNOSIS', 'DISCHARGE_LOCATION', 'DISCHTIME', 'EDOUTTIME',
       'EDREGTIME', 'ETHNICITY', 'HADM_ID', 'HAS_CHARTEVENTS_DATA',
       'HOSPITAL_EXPIRE_FLAG', 'INSURANCE', 'LANGUAGE', 'MARITAL_STATUS',
       'RELIGION', 'ROW_ID', 'SUBJECT_ID', 'atrial fibrillation',
       'blunt trauma', 'brain mass', 'chest pain', 'fever', 'hemoptysis',
       'hypotension', 'intracranial hemorrhage', 'intraparenchymal hemorrhage',
       'pancreatitis', 'pneumonia', 'pulmonary embolus', 's/p fall',
       'upper gastrointestinal bleed', 'upper gi bleed', 'hosp_duration'],
      dtype='object')

In [101]:
## Read patients
df_patients = pd.read_csv("./data/PATIENTS.csv")
# df2.set_index('City').subtract(df1.set_index('City'), fill_value=0)

In [16]:
adm_final_adj = adm_final[['SUBJECT_ID', 'ADMITTIME']]
adm_final_adj['ADMITTIME'] = adm_final_adj['ADMITTIME'].astype('datetime64[ns]')
df_patients_adj = df_patients[['SUBJECT_ID', 'DOB', 'GENDER']]
df_patients_adj = df_patients_adj.rename(index=str, columns={"DOB": "ADMITTIME"})
df_patients_adj['ADMITTIME'] = df_patients_adj['ADMITTIME'].astype('datetime64[ns]')

/usr/local/Cellar/ipython/7.0.1/libexec/vendor/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [153]:
adm_final_adj = adm_final.set_index('SUBJECT_ID')
df_patients_adj = df_patients.set_index('SUBJECT_ID')

In [154]:
age_days = (adm_final_adj['ADMITTIME'].astype('datetime64[ns]')).subtract(df_patients_adj['DOB'].astype('datetime64[ns]')).dropna()
year = age_days.dt.days

In [155]:
age = year//365

In [156]:
age = age.reset_index()

In [157]:
age = age.rename(index=str, columns={0:'age'})

In [158]:
print(len(adm_final))
adm_final = adm_final.join(age.set_index('SUBJECT_ID'), on='SUBJECT_ID')
print(len(adm_final))

14845
23009


In [110]:
adm_final.columns

Index(['ROW_ID', 'SUBJECT_ID', 'HADM_ID', 'ADMITTIME', 'DISCHTIME',
       'DEATHTIME', 'ADMISSION_TYPE', 'ADMISSION_LOCATION',
       'DISCHARGE_LOCATION', 'INSURANCE', 'LANGUAGE', 'RELIGION',
       'MARITAL_STATUS', 'ETHNICITY', 'EDREGTIME', 'EDOUTTIME', 'DIAGNOSIS',
       'HOSPITAL_EXPIRE_FLAG', 'HAS_CHARTEVENTS_DATA', 'age'],
      dtype='object')

In [218]:
adm_final

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
1          22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
7          28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
15         36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
22        456         357   174486  2197-12-06 07:13:00  2198-01-03 14:00:00   
39        473         368   105889  2137-07-11 17:56:00  2137-07-16 16:00:00   
44        478         372   144383  2114-07-08 17:22:00  2114-07-16 16:00:00   
57         55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
84         82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
101        99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
103       101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
136       175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
140       179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
145       184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
150       189         140   165618  2160-09-21 08:31:00  2160-09-23 12:00:00   
153       192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
154       193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
163       202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
197       153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
199       155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
220        10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
222        12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
228        18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
229        19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
235       383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
243       391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
265       413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
272       420         330   184134  2132-01-15 07:15:00  2132-01-17 10:30:00   
285       433         340   139131  2182-01-19 18:13:00  2182-02-11 13:25:00   
293       441         348   130789  2154-12-13 12:30:00  2154-12-16 11:31:00   
304       452         354   131861  2189-02-12 18:29:00  2189-03-02 14:09:00   
323       593         468   109718  2136-02-24 13:28:00  2136-03-12 18:29:00   
325       595         470   188804  2132-04-01 12:30:00  2132-04-06 16:00:00   
336       606         480   182365  2166-08-07 14:28:00  2166-08-18 18:39:00   
341       611         485   116665  2195-02-18 18:25:00  2195-02-25 16:20:00   
342       612         487   160958  2130-10-31 12:15:00  2130-11-04 19:46:00   
344       614         489   145439  2194-09-29 19:01:00  2194-10-07 18:05:00   
349       619         494   125330  2168-02-20 23:36:00  2168-03-02 16:15:00   
366       636         509   161218  2104-05-06 03:37:00  2104-05-19 16:30:00   
369       639         511   136962  2166-11-17 19:57:00  2166-11-24 13:10:00   
379       488         383   173723  2143-08-20 18:22:00  2143-09-13 14:30:00   
407       516         404   166989  2136-03-22 20:58:00  2136-03-23 00:40:00   
409       518         406   113900  2119-08-25 22:37:00  2119-09-01 18:00:00   
421       530         414   153627  2124-04-22 14:01:00  2124-05-02 04:45:00   
437       218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
439       220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
458       239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
459       240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
464       245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
480       261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
486    

In [53]:
adm_final = adm_final.reset_index(drop=True)

In [116]:
adm_final.age.value_counts()

89    555
78    234
72    228
65    227
82    225
68    222
77    220
58    218
66    217
61    217
64    217
69    212
62    210
79    210
80    205
76    202
71    202
60    196
84    194
70    194
67    193
63    193
55    192
73    189
57    188
75    187
83    186
53    181
81    178
52    176
     ... 
41     89
42     82
43     79
39     74
40     66
37     59
38     58
36     51
33     48
21     45
34     44
28     43
22     43
35     42
19     41
23     41
31     40
32     39
29     39
25     37
30     34
26     34
27     32
24     29
18     28
20     25
17     13
16      5
0       3
15      1
Name: age, Length: 76, dtype: int64

In [115]:
adm_final.age = adm_final.age.apply(lambda x: 89 if x < 0 else x)

In [172]:
print(len(p_final))
len(adm_final)

50303


10019

6618


AttributeError: 'DataFrame' object has no attribute 'FORM_VAL_DISP'

In [203]:
ms_new = ms.drop_duplicates(subset='SUBJECT_ID', keep='first')

In [206]:
ms_new = ms_new[['SUBJECT_ID', 'TOTAL_FORM_VAL_DISP_MAX']]
adm_final = adm_final.join(ms_new.set_index('SUBJECT_ID'), on='SUBJECT_ID')

In [210]:
adm_final.sort_values(by=['SUBJECT_ID'])

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
220        10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
222        12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
228        18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
229        19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
1          22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
7          28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
15         36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
57         55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
71         69          68   170467  2173-12-15 16:16:00  2174-01-03 18:30:00   
84         82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
101        99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
103       101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
118       116         109   183350  2137-11-04 19:36:00  2137-11-21 18:13:00   
197       153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
199       155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
136       175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
140       179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
145       184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
150       189         140   165618  2160-09-21 08:31:00  2160-09-23 12:00:00   
153       192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
154       193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
162       201         151   151029  2145-05-06 20:00:00  2145-05-15 17:30:00   
163       202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
437       218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
439       220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
458       239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
459       240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
464       245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
480       261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
486       267         202   108295  2145-10-22 01:31:00  2145-10-24 14:45:00   
492       273         209   135807  2119-09-21 19:57:00  2119-10-03 14:05:00   
495       276         211   193975  2196-03-11 15:46:00  2196-03-22 11:05:00   
498       279         213   179315  2122-02-13 04:38:00  2122-03-03 13:40:00   
512       293         224   169158  2151-04-01 08:06:00  2151-04-02 10:35:00   
514       295         226   108072  2196-12-15 12:37:00  2196-12-20 12:00:00   
519       300         231   198608  2176-05-14 21:12:00  2176-06-05 15:00:00   
529       310         238   174168  2198-06-28 07:15:00  2198-07-02 12:20:00   
530       311         239   127976  2175-01-12 07:15:00  2175-01-28 15:00:00   
545       326         252   190159  2133-03-31 04:24:00  2133-04-23 15:00:00   
561       342         266   186251  2168-07-10 08:01:00  2168-07-14 13:03:00   
562       343         267   163714  2156-06-04 05:08:00  2156-06-15 13:54:00   
563       344         268   110404  2198-02-11 13:40:00  2198-02-18 03:55:00   
571       352         276   135156  2147-11-19 16:53:00  2147-11-22 13:15:00   
593       374         295   192988  2176-03-06 12:30:00  2176-03-08 15:36:00   
596       377         298   119446  2140-08-07 00:33:00  2140-08-19 17:00:00   
235       383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
243       391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
265       413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
269       417         328   146586  2149-10-31 14:44:00  2149-11-06 15:24:00   
272    

In [124]:
adm_final.to_csv(path_or_buf="./data/admissions_processed.csv", index=False)

In [209]:
ms_new.sort_values(by=['SUBJECT_ID'])

SUBJECT_ID  TOTAL_FORM_VAL_DISP_MAX
646              11                    1.250
45               13                    2.000
971              20                    3.000
377              21                    2.000
1457             23                    0.400
1225             28                    0.400
2137             36                    3.000
2803             56                    0.500
3247             68                    0.520
4035             81                    1.000
5473             96                    1.000
5120             98                    2.000
8889            109                    1.000
8355            112                    0.500
9174            113                    0.900
10877           130                    0.400
9235            133                    0.400
12322           137                    3.000
8662            143                    1.000
11012           144                    0.500
15276           151                    2.000
11583           152                    0.400
10182           164                    1.000
14374           166                    1.500
15719           183                    6.800
11336           184                    1.000
10317           188                    0.400
16348           198                    1.000
14309           202                    1.000
18860           209                    0.400
14488           211                    0.400
14500           213                    0.500
22188           226                    0.500
18139           238                    3.000
16439           239                    0.400
20819           267                    3.000
19983           268                    1.000
22571           295                    0.750
20297           302                    1.000
24119           306                    6.000
23310           324                    1.000
24443           328                    1.000
24185           339                    1.000
25451           345                    3.000
23578           346                    0.250
29892           348                    1.000
28109           354                    3.000
28833           368                    1.000
27603           372                    0.400
31638           383                    0.250
30353           404                    1.000
32148           406                    2.400
27046           414                    0.500
30696           427                    2.000
30080           437                    0.520
30922           438                    0.030
34987           440                    0.530
39341           445                    0.500
35743           452                    1.000
37192           470                    1.000
38462           485                    1.000
39994           487                    0.400
38079           489                    0.400
34004           494                    0.500
42026           509                    0.500
41253           528                    1.000
37694           529                    1.000
39228           530                    0.400
42875           533                    3.500
43069           546                    0.500
40397           558                    1.000
43425           564                    3.000
41954           583                    2.000
40632           588                    0.750
44214           595                    4.000
44922           599                    3.000
44112           625                    1.000
47186           652                   15.800
50183           655                    1.000
50387           671                    2.000
50196           674                    3.000
48449           682                    0.800
47969           702                    0.400
51008           705                    0.500
51883           708                    2.000
51796           716                    2.000
51446           719                    1.400
57048           732                    1.000
5526

In [165]:
df3 = pd.read_csv("./data/admissions_processed.csv")

In [136]:
def df_to_X(df):
    
    # include age and hospital expire flag
    covariates = ['age', 'HOSPITAL_EXPIRE_FLAG']
    X = df[covariates]
    
    # include onehots for diagnosis
    diagnosis = pd.get_dummies(df.DIAGNOSIS)
    diagnosis.columns = ['DIAGNOSIS:%s' %d for d in diagnosis.columns]
    X = pd.concat([X, diagnosis], axis=1)
    
    # include duration of hosptial stay
    hosp_duration = (df['DISCHTIME'].astype('datetime64[ns]') - df['ADMITTIME'].astype('datetime64[ns]')).dt.days
    X['hosp_duration'] = hosp_duration
    
    # include onehots for insurance
    insur = pd.get_dummies(df.INSURANCE)
    insur.columns = ['INSURANCE:%s' %i for i in insur.columns]
    X = pd.concat([X, insur], axis=1)  

    
    # normalize duration because it is non-categorical
    d_mu = X['hosp_duration'].mean()
    d_std = X['hosp_duration'].std()
    X['hosp_duration'] = X['hosp_duration'].apply(lambda dp: (dp-d_mu)/d_std)

    # normalize age because non-categorical
    age_mu = X['age'].mean()
    age_std = X['age'].std()
    X['age'] = X['age'].apply(lambda age: (age-age_mu)/age_std)

    return X

In [168]:
X = df_to_X(df3)

0    8607
1    1412
Name: HOSPITAL_EXPIRE_FLAG, dtype: int64

In [198]:
ms.STARTDATE.value_counts()

2171-02-18 00:00:00    12
2118-07-11 00:00:00    11
2142-05-31 00:00:00    11
2191-04-12 00:00:00     9
2151-06-15 00:00:00     9
2142-08-10 00:00:00     9
2131-11-26 00:00:00     9
2188-12-24 00:00:00     9
2176-12-07 00:00:00     9
2165-07-19 00:00:00     8
2161-07-05 00:00:00     8
2117-06-27 00:00:00     8
2136-11-19 00:00:00     8
2124-12-12 00:00:00     8
2161-10-15 00:00:00     8
2198-09-19 00:00:00     8
2121-03-27 00:00:00     8
2162-03-04 00:00:00     8
2163-09-08 00:00:00     8
2136-11-02 00:00:00     8
2113-11-13 00:00:00     8
2117-11-19 00:00:00     8
2134-06-04 00:00:00     8
2149-06-10 00:00:00     8
2183-10-02 00:00:00     8
2189-01-06 00:00:00     8
2129-05-17 00:00:00     8
2184-09-08 00:00:00     8
2149-01-22 00:00:00     8
2142-08-08 00:00:00     7
2106-11-16 00:00:00     7
2171-03-12 00:00:00     7
2185-03-23 00:00:00     7
2120-12-31 00:00:00     7
2136-06-05 00:00:00     7
2124-11-14 00:00:00     7
2107-11-24 00:00:00     7
2101-12-28 00:00:00     7
2150-11-17 0

In [219]:
df3

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
0          22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
1          28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
2          36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
3         456         357   174486  2197-12-06 07:13:00  2198-01-03 14:00:00   
4         473         368   105889  2137-07-11 17:56:00  2137-07-16 16:00:00   
5         478         372   144383  2114-07-08 17:22:00  2114-07-16 16:00:00   
6          55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
7          82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
8          99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
9         101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
10        175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
11        179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
12        184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
13        189         140   165618  2160-09-21 08:31:00  2160-09-23 12:00:00   
14        192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
15        193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
16        202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
17        153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
18        155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
19         10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
20         12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
21         18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
22         19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
23        383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
24        391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
25        413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
26        420         330   184134  2132-01-15 07:15:00  2132-01-17 10:30:00   
27        433         340   139131  2182-01-19 18:13:00  2182-02-11 13:25:00   
28        441         348   130789  2154-12-13 12:30:00  2154-12-16 11:31:00   
29        452         354   131861  2189-02-12 18:29:00  2189-03-02 14:09:00   
30        593         468   109718  2136-02-24 13:28:00  2136-03-12 18:29:00   
31        595         470   188804  2132-04-01 12:30:00  2132-04-06 16:00:00   
32        606         480   182365  2166-08-07 14:28:00  2166-08-18 18:39:00   
33        611         485   116665  2195-02-18 18:25:00  2195-02-25 16:20:00   
34        612         487   160958  2130-10-31 12:15:00  2130-11-04 19:46:00   
35        614         489   145439  2194-09-29 19:01:00  2194-10-07 18:05:00   
36        619         494   125330  2168-02-20 23:36:00  2168-03-02 16:15:00   
37        636         509   161218  2104-05-06 03:37:00  2104-05-19 16:30:00   
38        639         511   136962  2166-11-17 19:57:00  2166-11-24 13:10:00   
39        488         383   173723  2143-08-20 18:22:00  2143-09-13 14:30:00   
40        516         404   166989  2136-03-22 20:58:00  2136-03-23 00:40:00   
41        518         406   113900  2119-08-25 22:37:00  2119-09-01 18:00:00   
42        530         414   153627  2124-04-22 14:01:00  2124-05-02 04:45:00   
43        218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
44        220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
45        239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
46        240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
47        245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
48        261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
49     

In [222]:
ms = df2[df2.DRUG=='Morphine Sulfate']
ms_id = ms.HADM_ID.unique()
ms_adm = df3[df3.HADM_ID.isin(ms_id)]
ms_adm.ETHNICITY.value_counts()

WHITE       5579
BLACK        514
HISPANIC     292
ASIAN        233
Name: ETHNICITY, dtype: int64

In [237]:
ms_adm['drug'] = "Morphine Sulfate"
ms_adm

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
19         10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
20         12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
21         18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
22         19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
0          22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
1          28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
2          36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
6          55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
8370       69          68   170467  2173-12-15 16:16:00  2174-01-03 18:30:00   
7          82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
8          99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
9         101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
8371      116         109   183350  2137-11-04 19:36:00  2137-11-21 18:13:00   
17        153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
18        155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
10        175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
11        179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
12        184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
14        192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
15        193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
8372      201         151   151029  2145-05-06 20:00:00  2145-05-15 17:30:00   
16        202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
43        218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
44        220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
45        239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
46        240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
47        245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
48        261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
49        267         202   108295  2145-10-22 01:31:00  2145-10-24 14:45:00   
50        273         209   135807  2119-09-21 19:57:00  2119-10-03 14:05:00   
51        276         211   193975  2196-03-11 15:46:00  2196-03-22 11:05:00   
52        279         213   179315  2122-02-13 04:38:00  2122-03-03 13:40:00   
9571      295         226   108072  2196-12-15 12:37:00  2196-12-20 12:00:00   
55        310         238   174168  2198-06-28 07:15:00  2198-07-02 12:20:00   
56        311         239   127976  2175-01-12 07:15:00  2175-01-28 15:00:00   
9237      343         267   163714  2156-06-04 05:08:00  2156-06-15 13:54:00   
9572      344         268   110404  2198-02-11 13:40:00  2198-02-18 03:55:00   
59        374         295   192988  2176-03-06 12:30:00  2176-03-08 15:36:00   
23        383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
24        391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
25        413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
9569      417         328   146586  2149-10-31 14:44:00  2149-11-06 15:24:00   
8373      430         339   112625  2187-04-20 23:10:00  2187-06-19 13:20:00   
9570      437         345   169339  2169-05-21 22:03:00  2169-05-31 14:30:00   
8374      438         346   186516  2148-11-30 13:37:00  2148-12-10 15:00:00   
28        441         348   130789  2154-12-13 12:30:00  2154-12-16 11:31:00   
29        452         354   131861  2189-02-12 18:29:00  2189-03-02 14:09:00   
4         473         368   105889  2137-07-11 17:56:00  2137-07-16 16:00:00   
5         478         372   144383  2114-07-08 17:22:00  2114-07-16 16:00:00   
39     

In [ ]:

print(len(ms))
def extract_max(val):
    val = str(val)
    a = val.split('-')
    return float(a[-1])
ms['FORM_VAL_DISP_MAX'] =  ms.FORM_VAL_DISP.apply(extract_max)
ms['TOTAL_FORM_VAL_DISP_MAX'] = ms.groupby(['SUBJECT_ID', 'STARTDATE'])['FORM_VAL_DISP_MAX'].transform('sum')

In [240]:
ms_adm.to_csv(path_or_buf="./data/admissions_processed_morphine_sulfate.csv", index=False)

In [241]:
df4 = pd.read_csv("./data/admissions_processed_morphine_sulfate.csv")
df4

ROW_ID  SUBJECT_ID  HADM_ID            ADMITTIME            DISCHTIME  \
0         10          11   194540  2178-04-16 06:18:00  2178-05-11 19:00:00   
1         12          13   143045  2167-01-08 18:43:00  2167-01-15 15:15:00   
2         18          20   157681  2183-04-28 09:45:00  2183-05-03 14:45:00   
3         19          21   109451  2134-09-11 12:17:00  2134-09-24 16:15:00   
4         22          23   152223  2153-09-03 07:15:00  2153-09-08 19:10:00   
5         28          28   162569  2177-09-01 07:15:00  2177-09-06 16:00:00   
6         36          36   182104  2131-04-30 07:15:00  2131-05-08 14:00:00   
7         55          56   181711  2104-01-02 02:01:00  2104-01-08 10:30:00   
8         69          68   170467  2173-12-15 16:16:00  2174-01-03 18:30:00   
9         82          81   175016  2192-01-09 18:50:00  2192-01-11 13:00:00   
10        99          96   170324  2156-03-31 16:11:00  2156-04-29 15:05:00   
11       101          98   188606  2137-04-02 08:00:00  2137-04-09 10:38:00   
12       116         109   183350  2137-11-04 19:36:00  2137-11-21 18:13:00   
13       153         112   174105  2194-06-13 18:39:00  2194-06-18 16:50:00   
14       155         113   109976  2140-12-12 22:46:00  2140-12-27 19:30:00   
15       175         130   198214  2119-10-29 14:49:00  2119-11-05 17:00:00   
16       179         133   191817  2165-05-06 18:38:00  2165-05-16 15:25:00   
17       184         137   151583  2191-11-10 13:57:00  2191-11-24 12:23:00   
18       192         143   143808  2155-01-17 21:40:00  2155-02-02 15:00:00   
19       193         144   137432  2197-07-14 20:18:00  2197-08-01 13:15:00   
20       201         151   151029  2145-05-06 20:00:00  2145-05-15 17:30:00   
21       202         152   117181  2145-07-22 11:00:00  2145-08-03 11:20:00   
22       218         164   182743  2116-12-28 15:32:00  2117-01-16 03:20:00   
23       220         166   128219  2105-01-23 22:57:00  2105-01-24 03:48:00   
24       239         183   113341  2188-07-03 16:41:00  2188-07-05 17:30:00   
25       240         184   137477  2168-03-13 19:00:00  2168-03-16 15:45:00   
26       245         188   160697  2157-01-11 16:56:00  2157-01-19 14:58:00   
27       261         198   131286  2181-10-05 22:04:00  2181-10-24 16:40:00   
28       267         202   108295  2145-10-22 01:31:00  2145-10-24 14:45:00   
29       273         209   135807  2119-09-21 19:57:00  2119-10-03 14:05:00   
30       276         211   193975  2196-03-11 15:46:00  2196-03-22 11:05:00   
31       279         213   179315  2122-02-13 04:38:00  2122-03-03 13:40:00   
32       295         226   108072  2196-12-15 12:37:00  2196-12-20 12:00:00   
33       310         238   174168  2198-06-28 07:15:00  2198-07-02 12:20:00   
34       311         239   127976  2175-01-12 07:15:00  2175-01-28 15:00:00   
35       343         267   163714  2156-06-04 05:08:00  2156-06-15 13:54:00   
36       344         268   110404  2198-02-11 13:40:00  2198-02-18 03:55:00   
37       374         295   192988  2176-03-06 12:30:00  2176-03-08 15:36:00   
38       383         302   191028  2133-03-29 02:33:00  2133-04-01 12:15:00   
39       391         306   167129  2199-09-15 19:59:00  2199-09-21 14:00:00   
40       413         324   146127  2199-10-16 01:11:00  2199-10-16 17:19:00   
41       417         328   146586  2149-10-31 14:44:00  2149-11-06 15:24:00   
42       430         339   112625  2187-04-20 23:10:00  2187-06-19 13:20:00   
43       437         345   169339  2169-05-21 22:03:00  2169-05-31 14:30:00   
44       438         346   186516  2148-11-30 13:37:00  2148-12-10 15:00:00   
45       441         348   130789  2154-12-13 12:30:00  2154-12-16 11:31:00   
46       452         354   131861  2189-02-12 18:29:00  2189-03-02 14:09:00   
47       473         368   105889  2137-07-11 17:56:00  2137-07-16 16:00:00   
48       478         372   144383  2114-07-08 17:22:00  2114-07-16 16:00:00   
49       488         383   173723  2143-08-20 18:22:00  

In [245]:
def df_to_X(df):
    
    # include age and hospital expire flag
    covariates = ['age', 'HOSPITAL_EXPIRE_FLAG']
    X = df[covariates]
    
    # include onehots for diagnosis
    diagnosis = pd.get_dummies(df.DIAGNOSIS)
    diagnosis.columns = ['DIAGNOSIS:%s' %d for d in diagnosis.columns]
    X = pd.concat([X, diagnosis], axis=1)
    
    # include duration of hosptial stay
    hosp_duration = (df['DISCHTIME'].astype('datetime64[ns]') - df['ADMITTIME'].astype('datetime64[ns]')).dt.days
    X['hosp_duration'] = hosp_duration
    
    # include onehots for insurance
    insur = pd.get_dummies(df.INSURANCE)
    insur.columns = ['INSURANCE:%s' %i for i in insur.columns]
    X = pd.concat([X, insur], axis=1)  

    
    # normalize duration because it is non-categorical
    d_mu = X['hosp_duration'].mean()
    d_std = X['hosp_duration'].std()
    X['hosp_duration'] = X['hosp_duration'].apply(lambda dp: (dp-d_mu)/d_std)

    # normalize age because non-categorical
    age_mu = X['age'].mean()
    age_std = X['age'].std()
    X['age'] = X['age'].apply(lambda age: (age-age_mu)/age_std)

    return X

def df_to_T(df, eth):
    return df['ETHNICITY'].apply(lambda x: int(x==eth))

def df_to_Y(df):
    return df['TOTAL_FORM_VAL_DISP_MAX']

In [246]:
X = df_to_X(df4)
T = df_to_T(df4, 'WHITE')
Y = df_to_Y(df4)
print('X: ', X.shape)
print("T: ", T.shape)
print("Y: ", Y.shape)

X:  (6618, 122)
T:  (6618,)
Y:  (6618,)
